In [1]:
import pandas as pd
import numpy as np
import re
#natural language processing library
import spacy
from collections import Counter
data1 = pd.read_csv('FirstDatasetFull.csv')

C:\Users\egatzinski\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3444: DtypeWarning: Columns (13) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [2]:
#removing rows that contain NULL values
data1 = data1.dropna(thresh=3)
data1 = data1.reset_index()

# Organising Displaced Columns

In [3]:
i = 0
while i < len(data1):
    #displaced columns are marked with '/'
    if '/' in data1['STOCK'][i]:
        n = len(data1.columns) - 1
        while n >= 2:
            data1[data1.columns[n]][i] = data1[data1.columns[n - 1]][i]
            n -= 1
    i +=1
    print(i)

C:\Users\EGATZI~1\AppData\Local\Temp/ipykernel_94284/2195589202.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data1[data1.columns[n]][i] = data1[data1.columns[n - 1]][i]


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


# Data pre-processing

In [4]:
#Checking the companies with the most occurrences in the dataset
data1['STOCK'].value_counts().head(6)


eBay       5789
Nike       4664
Reuters    4575
Netflix    3489
Amazon     2944
Apple      2891
Name: STOCK, dtype: int64

In [5]:
#storing the top 6 firms in a variable
topfirms1 = ['eBay', 'Nike', 'Reuters', 'Netflix', 'Amazon', 'Apple']

In [6]:
# making sure that the dataset only contains the top 6 companies
#resetting the index of the dataframe
data1 = data1[data1['STOCK'].isin(topfirms1)].reset_index()

In [7]:
#making sure that there are no values which are null in the 'TWEETS' column
data1 = data1[data1['TWEET'].notnull()]
data1 = data1.drop(columns = ['level_0'])
data1 = data1.reset_index()

In [8]:
#regular expression
import re
#data cleaning
data1['TWEET'] = data1['TWEET'].apply(lambda x : re.sub(r"(?:\@|https?\://)\S+", "", x))
data1['TWEET'] = data1['TWEET'].apply(lambda x : x.replace('RT', ''))
#creating two columns which check for the number of words in a tweet and number of letters in a tweet, respectively
data1['WordsPerTweet'] = data1['TWEET'].apply(lambda x : len(x.split(' ')))
data1['LettersPerTweet'] = data1['TWEET'].apply(lambda x : len(x))

In [9]:
#dropping irrelevant columns
data1 = data1.drop(columns = ['level_0', 'index', 'Unnamed: 0', '1_DAY_RETURN', '2_DAY_RETURN', '3_DAY_RETURN', 'MENTION'])

In [10]:
data1['tuple'] = list(zip(data1['STOCK'], data1['DATE']))

In [11]:
#grouping the data set by stock
tweetsday = data1.groupby(['STOCK', 'DATE'])['TWEET'].count().to_frame().reset_index()

In [12]:
tweetsday['tuple'] = list(zip(tweetsday['STOCK'], tweetsday['DATE']))

In [13]:
dictdays = dict(zip(tweetsday['tuple'], tweetsday['TWEET']))

In [14]:
#creating a column which check the number of tweets that were released in a given day
data1['Tweets in a day'] = data1['tuple'].apply(lambda x : dictdays[x])

In [15]:
data1 = data1.drop(columns = ['tuple'])

# Part-of-speech tagging

In [16]:
#loading a natural language processing english dictionary
nlp = spacy.load("en_core_web_sm")
#adding the textual features
columns = ['new_text', 'pos', 'tag']
listOfLists = []
#iterating through the whole dataset to perform part-of-speech tagging
for i in range(0, len(data1)):
    listOfLists.append([])
for column in columns:
    data1[column] = listOfLists
for column in columns:
    i = 0
    while i < len(data1):
        values = []
        for token in nlp(data1['TWEET'][i]):
            if column == 'new_text':
                values.append(token.text)
            elif column == 'pos':
                values.append(token.pos_)
            elif column == 'tag':
                values.append(token.tag_)
     
        print(values)
        if column != 'new_text' : 
            values = Counter(values)
        data1[column][i] = values
        i += 1
    print(column)


[' ', 'has', 'your', 'back', 'when', 'it', 'comes', 'to', 'food', 'shopping', 'with', 'tech', 'replacing', 'queues', ',', 'just', 'grab', 'and', 'go', '\r']
['      ', 'Did', 'you', 'read', 'the', 'article', ',', 'Einstein', '?', '\r']
['  ', 'Welcome', ' ', '#', 'ACLU', ',', '#', 'AAAI', ',', '    ', 'to', 'the', ' ', 'board', 'of', 'Trustees', '!', 'Info', ':', '…', '\r']
['Canadian', ' ', '#', 'shoppers', 'call', 'for', 'tax', 'free', 'shipments', '\r\r\r\r\r\r\n', '#', 'retail', '#', 'intelligence', '#', 'canada', '\r\r\r\r\r\r\n\r']
['  ', 'COVER', 'THIS', ',', '\r\r\r\r\r\r\n          \r']
['Check', 'out', '       ', 'BOTANICAL', '   ', 'SILK', '  ', 'HAIRSPRAY', ',', 'STYLE', ' ', 'SIGN', '   ', 'SPRAY', '#', 'JOHNAMICO', ' ', 'via', '\r']
['  ', 'How', 'Toyota', ',', 'Target', ',', 'Best', 'Buy', 'are', 'fighting', 'back', 'against', 'Republican', 'border', 'tax', 'push', ' \r']
['  ', 'Saudi', 'king', 'agrees', 'in', 'call', 'with', 'Trump', 'to', 'support', 'Syria', ',', 'Yem

C:\Users\EGATZI~1\AppData\Local\Temp/ipykernel_94284/244248802.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data1[column][i] = values


[' ', 'lol', 'u', 'ca', "n't", 'even', 'stand', 'up', 'to', 'big', 'bad', 'Russia', 'on', 'ur', 'own', ',', 'gimme', 'a', 'break', ',', '\r']
['Check', 'out', 'Belwith', '1', '1/4', '"', 'Mushroom', 'Knob', 'P2511', '-', 'WOA', 'Lot', 'of', '12', 'Knobs', '#', 'Belwith', ' ', 'via', '\r']
['U.S.', 'will', 'change', 'course', 'on', 'climate', 'policy', ',', 'says', 'former', 'EPA', 'transition', 'head', ' ', 'via', '\r']
[' \r\r\r\r\r\r\n', '#', 'SaveFakingIt', '\r\r\r\r\r\r\n', '#', 'SaveFakingIt', '\r\r\r\r\r\r\n', 'Please', 'Save', 'Faking', 'It', '\r']
['Check', 'out', 'Long', 'ALFANI', 'Geo', 'Pendant', 'Gold', 'Hematite', 'metal', 'Herringbone', 'Gold', 'tone', 'Chain', 'NEW', '32', '"', ' ', '#', 'ALFANI', ' ', 'via', '\r']
['Check', 'out', '80', 'TILE', 'GRAMMAR', ',', 'SENTENCE', 'BUILDING', 'LEARNING', 'SET', ',', 'COLOR', 'CODED', ',', 'NEW', '  ', 'via', '\r']
['  ', 'Check', 'out', '2004', 'Star', 'Wars', 'Trilogy', 'Collection', 'Large', 'Size', 'Boba', 'Fett', '12', '"', 

In [17]:
poskeys = list()
for value in data1['pos']:
    for key in value.keys():
        poskeys.append(key)
poskeys = set(poskeys)
print(poskeys)
for wordtype in poskeys:
    data1['{}'.format(wordtype)] = 0
i = 0
while i < len(data1):

    for column in data1.columns[16:]:
        data1[column][i] = data1['pos'][i][column]



    i += 1
    
    
    

{'SCONJ', 'INTJ', 'PRON', 'VERB', 'ADV', 'ADP', 'CCONJ', 'PROPN', 'PUNCT', 'PART', 'ADJ', 'NOUN', 'DET', 'NUM', 'X', 'AUX', 'SYM', 'SPACE'}


C:\Users\EGATZI~1\AppData\Local\Temp/ipykernel_94284/3763963714.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data1[column][i] = data1['pos'][i][column]


In [18]:
data1

TWEET    STOCK        DATE  \
0       has your back when it comes to food shopping ...   Amazon  31/01/2017   
1                  Did you read the article, Einstein?\r  Reuters  31/01/2017   
2        Welcome  #ACLU, #AAAI,     to the  board of ...    Apple  31/01/2017   
3      Canadian  #shoppers call for tax free shipment...     eBay  31/01/2017   
4                  COVER THIS,\r\r\r\r\r\r\n          \r  Reuters  31/01/2017   
...                                                  ...      ...         ...   
13929    'History will judge her on her response,' Am...  Reuters  29/09/2018   
13930    OUT NOW!\r\r\r\r\r\r\nBarnes &amp; Noble,   ...   Amazon  29/09/2018   
13931  I really can’t believe same day Amazon Prime s...   Amazon  29/09/2018   
13932    'This conviction is a travesty of justice' -...  Reuters  29/09/2018   
13933    OUT NOW!\r\r\r\r\r\r\nBarnes &amp; Noble,   ...   Amazon  30/09/2018   

       LAST_PRICE  7_DAY_RETURN   PX_VOLUME  VOLATILITY_10D  VOLATILITY_30D  \
0        823.4800     -0.001263   3137196.0          13.447          16.992   
1         49.3887      0.004461    547029.0           9.665           9.094   
2        121.3500     -0.011372  49200993.0           9.114           8.417   
3         31.8300     -0.057807   9469076.0          33.029          22.932   
4         49.3887      0.004461    547029.0           9.665           9.094   
...           ...           ...         ...             ...             ...   
13929     50.3139     -0.006785   7988967.0           6.838          12.771   
13930   2003.0000     -0.043929   4085135.0          20.709          22.946   
13931   2003.0000     -0.043929   4085135.0          20.709          22.946   
13932     50.3139     -0.006785   7988967.0           6.838          12.771   
13933   2003.0000     -0.043929   4085135.0          20.709          22.946   

      LSTM_POLARITY    TEXTBLOB_POLARITY  ...  PUNCT  PART  ADJ NOUN DET NUM  \
0                -1                  0.0  ...      1     0    0    5   0   0   
1                 1                  0.0  ...      2     0    0    1   1   0   
2                 1                  1.0  ...      5     0    0    2   1   0   
3                 1                  0.4  ...      0     0    3    5   0   0   
4                 1                  0.0  ...      1     0    0    0   0   0   
...             ...                  ...  ...    ...   ...  ...  ...  ..  ..   
13929             1                  0.0  ...      2     1    0    3   0   0   
13930             1                  0.6  ...      8     0    1    1   0   0   
13931            -1  0.26666666666666666  ...      2     1    1    4   2   0   
13932             1                  0.0  ...      4     0    0    5   2   0   
13933             1                  0.6  ...      8     0    1    1   0   0   

       X  AUX  SYM  SPACE  
0      0    0    0      2  
1      0    1    0      2  
2      0    0    2      5  
3      0    0    1      3  
4      0    0    0      2  
...   ..  ...  ...    ...  
13929  0    1    0      2  
13930  0    0    0      8  
13931  0    2    0      2  
13932  0    1    0      2  
13933  0    0    0      8  

[13934 rows x 34 columns]